In [1]:
import pandas as pd
import numpy as np
import altair as alt
import geopandas as gpd
import json

In [2]:
# Loading datasets 
crop_df = pd.read_csv('pmfby-district-level.csv')
farmer_pop = pd.read_csv('farmer_pop.csv')
geo_df = gpd.read_file('in_shp/in.shp')

In [ ]:
# Mapping agricultural zones 
zones = {
    'North Zone': ['Himachal Pradesh', 'Punjab', 'Uttarakhand', 'Uttar Pradesh', 'Haryana', 'Rajasthan'],
    'South Zone': ['Andhra Pradesh', 'Telangana', 'Karnataka', 'Kerala', 'Tamil Nadu'],
    'East Zone': ['Bihar', 'Jharkhand', 'Odisha', 'West Bengal'],
    'West Zone': ['Goa', 'Gujarat', 'Maharashtra'],
    'Central Zone': ['Madhya Pradesh', 'Chhattisgarh'],
    'North East Zone': ['Arunachal Pradesh', 'Assam', 'Meghalaya', 'Manipur', 'Mizoram', 'Nagaland', 'Sikkim', 'Tripura']
}

# Normalize helper and build lookup
def norm(s):
    if pd.isna(s): return s
    s2 = " ".join(str(s).replace('\xa0', ' ').split())
    return s2.strip().lower()
lookup = {norm(st): zone for zone, states in zones.items() for st in states}

# Assign zones
crop_df['zones'] = crop_df['state_name'].apply(lambda x: lookup.get(norm(x), pd.NA))

# Keep only mapped states
crop_df = crop_df[crop_df['zones'].notna()].copy()

# Create season flag for Kharif=1 and Rabi=0
crop_df['season_flag'] = crop_df['season'].map({'Kharif': 1, 'Rabi': 0})

# Aggregating variabels 
count_variables = [
    'farmer_count', 'loanee', 'non_loanee', 'area_insured', 'sum_insured',
    'farmer_share', 'goi_share', 'state_share', 'iu_count', 'gross_premium'
]
percent_variables = [
    'male', 'female', 'transgender', 'sc', 'st', 'obc', 'gen',
    'marginal', 'small', 'other'
]

# Aggregate count type variables
grouped_counts = (
    crop_df.groupby(['year', 'season_flag', 'state_name', 'district_name', 'district_code', 'zones'])
    .agg({**{var: 'sum' for var in count_variables},
          'scheme': lambda x: x.mode()[0] if len(x.mode()) > 0 else x.iloc[0]})
    .reset_index()
)

# Weighted averages for percentage variables
def calculate_weighted_averages(group):
    result = {}
    for var in percent_variables:
        if var in group.columns:
            w = group['farmer_count']
            v = group[var]
            result[var] = np.average(v, weights=w) if w.sum() > 0 else v.mean()
    return pd.Series(result)

weighted_percentages = (
    crop_df.groupby(['year', 'season_flag', 'state_name', 'district_name', 'district_code', 'zones'])
    .apply(calculate_weighted_averages)
    .reset_index()
)

# Merge counts and percentages
grouped_insurance = pd.merge(
    grouped_counts,
    weighted_percentages,
    on=['year', 'season_flag', 'state_name', 'district_name', 'district_code', 'zones'],
    how='left'
)


/var/folders/bq/92m03xln47dgq4zww9kqjvhh0000gn/T/ipykernel_85722/4015692691.py:57: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(calculate_weighted_averages)


In [8]:
# Rename from farmer pop dataset
farmer_pop['state_name'] = farmer_pop['State/UT'].str.strip()

# Compute total farmers 
farmer_pop['total_farmers'] = (
    farmer_pop['Marginal'] +
    farmer_pop['Small'] +
    (farmer_pop['Other'] if 'Other' in farmer_pop.columns else 0)
)

# Limit to only states in zone list/insurance data 
valid_states = grouped_insurance['state_name'].unique()
farmer_population = farmer_pop[farmer_pop['state_name'].isin(valid_states)].copy()

# Merge farmer population data with existing grouped_insurance dataframe 
merged_final = pd.merge(
    grouped_insurance,
    farmer_population[['state_name', 'total_farmers', 'Marginal', 'Small']],
    on='state_name',
    how='left'
)

# Calculate insurance penetration (percent of farmers insured)
merged_final['insurance_penetration'] = (
    merged_final['farmer_count'] / merged_final['total_farmers'] * 100
)

# Drop all_state carried from farmer population 
merged_final = merged_final[merged_final['state_name'].str.lower() != 'all_state']

# Round numeric columns
merged_final = merged_final.round(2)

# See the results 
print(merged_final.shape)
merged_final.head()


(3897, 31)


year  season_flag      state_name  district_name  district_code  \
0  2018            0  Andhra Pradesh      Anantapur          502.0   
1  2018            0  Andhra Pradesh       Chittoor          503.0   
2  2018            0  Andhra Pradesh  East Godavari          505.0   
3  2018            0  Andhra Pradesh         Guntur          506.0   
4  2018            0  Andhra Pradesh        Krishna          510.0   

        zones  farmer_count   loanee  non_loanee  area_insured  ...    st  \
0  South Zone       59776.0   7073.0     98303.0        143.99  ...  0.52   
1  South Zone       20504.0  13718.0      9238.0        229.73  ...  1.47   
2  South Zone        9434.0   9843.0       950.0         18.95  ...  2.92   
3  South Zone        7352.0   6650.0      2688.0          7.78  ...  0.47   
4  South Zone        4782.0   4791.0      1755.0         27.65  ...  0.60   

     obc    gen  marginal  small  other total_farmers  Marginal    Small  \
0  34.33  61.48     14.99  69.90  15.11       7550285   5904039  1646246   
1  36.09  56.65     24.41  64.50  11.09       7550285   5904039  1646246   
2  42.83  51.24     26.27  54.98  18.75       7550285   5904039  1646246   
3  42.85  51.96     22.72  69.92   7.36       7550285   5904039  1646246   
4  35.55  58.66     28.85  49.55  21.60       7550285   5904039  1646246   

   insurance_penetration  
0                   0.79  
1                   0.27  
2                   0.12  
3                   0.10  
4                   0.06  

[5 rows x 31 columns]

In [9]:
# Aggregate district level data into zone-level totals and averages
plot_df = (
    merged_final.groupby(['zones', 'year', 'season_flag'], as_index=False)
    .agg({
        'farmer_count': 'sum',
        'insurance_penetration': 'mean'
    })
)

In [12]:
# Aggregate data to state-year-season level
final_merged_data = merged_final.groupby(['state_name', 'year', 'season_flag']).agg({
    'zones': 'first',
    'farmer_count': 'sum',
    'loanee': 'sum',
    'non_loanee': 'sum',
    'area_insured': 'sum',
    'sum_insured': 'sum',
    'farmer_share': 'sum',
    'goi_share': 'sum',
    'state_share': 'sum',
    'iu_count': 'sum',
    'gross_premium': 'sum',
    'male': 'mean',
    'female': 'mean',
    'transgender': 'mean',
    'sc': 'mean',
    'st': 'mean',
    'obc': 'mean',
    'gen': 'mean',
    'marginal': 'mean',  
    'small': 'mean',
    'other': 'mean',
    'total_farmers': 'mean',
    'Marginal': 'mean', 
    'Small': 'mean',
    'insurance_penetration': 'mean'
}).reset_index()


In [13]:
# Create season_year variable
final_merged_data['season_year'] = (
    final_merged_data['year'].astype(str) + ' ' + 
    final_merged_data['season_flag'].map({1: 'Kharif', 0: 'Rabi'})
)

In [ ]:
# Cleaning and merging geo data 
# Create a mapping dictionary to standardize state names as they are misaligned with the geo data 
state_mapping = {
    'Andaman and Nicobar': 'Andaman and Nicobar Islands',
    'Orissa': 'Odisha',
    'Uttaranchal': 'Uttarakhand',
    'DÄ\x81dra and Nagar Haveli and DamÄ\x81n and Diu': 'Dadra and Nagar Haveli and Daman and Diu',
    'Delhi': 'NCT of Delhi',
}

# Apply mapping to geo_df
geo_df['name_clean'] = geo_df['name'].replace(state_mapping)

# Merge 
merged_geo_df = geo_df.merge(
    final_merged_data,
    left_on='name_clean',
    right_on='state_name',
    how='left'
)

# States from geo data taht did not find a match in insurance data 
unmatched_states = merged_geo_df[merged_geo_df['state_name'].isna()]['name'].unique()
print(f"States without insurance data: {unmatched_states}")

States without insurance data: ['Andaman and Nicobar' 'Arunachal Pradesh' 'Bihar' 'Chandigarh'
 'DÄ\x81dra and Nagar Haveli and DamÄ\x81n and Diu' 'Delhi' 'Mizoram'
 'Nagaland' 'Puducherry' 'Punjab' 'Lakshadweep' 'Jammu and Kashmir'
 'Ladakh']


In [ ]:
# Convert geodf data to GeoJSON 
merged_geo_json = json.loads(merged_geo_df.to_json())
geo_data = alt.Data(values=merged_geo_json['features'])

# Custom colors for each zone. These colors will be used throughout this project for these zones. 
# Asked LLMs how to create a custom color scheme for color scale in altair. 
custom_colors = {
    'North Zone': '#3594cc',      # Blueish
    'South Zone': '#fc8d59',      # Orangeish
    'East Zone': '#91cf60',       # Greenish
    'West Zone': '#c46666',       # Maroonish
    'Central Zone': '#eece00',    # Yellowish
    'North East Zone': '#54a1a1'  # Tealish
}

# Scale with custom domain and range
zone_colors = alt.Scale(
    domain=list(custom_colors.keys()),
    range=list(custom_colors.values())
)

# Base map 
base_map = alt.Chart(geo_data).mark_geoshape(
    stroke='black',
    strokeWidth=0.2,
    fill='lightgray'  
).project(
    'equirectangular'
)

# Zone layer 
zones_layer = alt.Chart(geo_data).mark_geoshape(
    stroke='black',
    strokeWidth=0.2
).encode(
    color=alt.Color('properties.zones:N', 
                   title='Zone',
                   scale=zone_colors)
)

# combine 
zones_map = alt.layer(
    base_map,
    zones_layer
).properties(
    title='Agricultural Zones in India',
    width=600,
    height=600
)

zones_map

alt.LayerChart(...)

In [19]:
# Map of North Eastern states only 

# NE States shapes 
ne_states = [
    "Arunachal Pradesh",
    "Assam",
    "Manipur",
    "Meghalaya",
    "Mizoram",
    "Nagaland",
    "Sikkim",
    "Tripura"
]
ne_geo_all = geo_df[geo_df['name_clean'].isin(ne_states)].copy()

# merge 
ne_geo_merged = ne_geo_all.merge(
    final_merged_data,
    left_on='name_clean',
    right_on='state_name',
    how='left'  
)

# Color only if has insurance data 
ne_geo_merged['has_data'] = ne_geo_merged['state_name'].notna()

# Labels within states 
ne_geo_merged['centroid_lon'] = ne_geo_merged.geometry.centroid.x
ne_geo_merged['centroid_lat'] = ne_geo_merged.geometry.centroid.y

# Color based on data 
color_scale = alt.Scale(
    domain=[True, False],
    range=['#54a1a1', 'lightgray'] 
)

# Base layer
base_map = alt.Chart(ne_geo_merged).mark_geoshape(
    stroke='black',
    strokeWidth=0.5
).encode(
    color=alt.Color(
        'has_data:N',
        title='Data Availability',
        scale=color_scale,
        legend=alt.Legend(labelExpr="datum.label == 'true' ? 'Has data' : 'No data'")
    )
).project('equirectangular')

# Text on map 
text_layer = alt.Chart(ne_geo_merged).mark_text(
    fontSize=10,
    fontWeight='bold',
    color='black'
).encode(
    longitude='centroid_lon:Q',
    latitude='centroid_lat:Q',
    text='name_clean:N'
)

# Combined map 
ne_map = alt.layer(
    base_map,
    text_layer
).properties(
    title='North Eastern States of India',
    width=400,
    height=400
).configure_title(
    offset=20
)

ne_map


/var/folders/bq/92m03xln47dgq4zww9kqjvhh0000gn/T/ipykernel_85722/1224985385.py:28: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  ne_geo_merged['centroid_lon'] = ne_geo_merged.geometry.centroid.x
/var/folders/bq/92m03xln47dgq4zww9kqjvhh0000gn/T/ipykernel_85722/1224985385.py:29: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  ne_geo_merged['centroid_lat'] = ne_geo_merged.geometry.centroid.y


alt.LayerChart(...)

In [ ]:
# India and Zone wide trends 
zone_season = (final_merged_data
             .groupby(['zones', 'season_year'], as_index=False)
             .agg({'insurance_penetration':'mean'}))

# India agerage per season 
india_season = (final_merged_data
               .groupby(['season_year'], as_index=False)
               .agg({'insurance_penetration':'mean'}))
india_season['zones'] = 'India Total'

# Data for this chart 
combined_data = pd.concat([zone_season, india_season], ignore_index=True)

# Cumulative insurance penetration for each zone and India
combined_data = combined_data.sort_values(['zones', 'season_year'])
combined_data['cumulative_penetration'] = combined_data.groupby('zones')['insurance_penetration'].cumsum()

# Plot
cumulative_chart = alt.Chart(combined_data).mark_line(point=True, strokeWidth=3).encode(
    x=alt.X('season_year:O', title='Season - Year', axis=alt.Axis(labelAngle=0)),
    y=alt.Y('cumulative_penetration:Q', title='Cumulative Insurance Penetration'),
    color=alt.Color('zones:N', title='Zone', scale=color_scale),
    strokeDash=alt.condition(
        alt.datum.zones == 'India Total',
        alt.value([2, 2]),  
        alt.value([0])
    ) # Asked LLM how to create one of the lines in a line chart dashed. 
).properties(
    title='Cumulative Insurance Penetration by Zone Over Time (India Dashed)',
    width=700,
    height=500
)

cumulative_chart

alt.Chart(...)

In [ ]:
# Total number of farmers insured 
chart_farmers = (
    alt.Chart(final_merged_data)
    .mark_bar()
    .encode(
        x=alt.X('zones:N', title=None,
                 sort=alt.EncodingSortField('farmer_count', op='sum', order='descending')),
        y=alt.Y('farmer_count:Q', title='Total Farmers Insured'),
        color=alt.Color('zones:N', title='Zone', 
                       scale=zone_colors, 
                       legend=alt.Legend(title='Zone', orient='right')),
        opacity=alt.Opacity('year:O', title='Year',
                           scale=alt.Scale(domain=sorted(final_merged_data['year'].unique()), 
                                         range=[1.0, 0.7, 0.4, 0.2])), #Asked LLMS how to implement Altair condition color opacity. 
        xOffset='year:O'
    )
    .properties(
        title='Total Farmers Insured by Zone and Year',
        width=400,
        height=300
    )
)

# Insurance penetration by zone 
chart_penetration = (
    alt.Chart(final_merged_data)
    .mark_bar()
    .encode(
        x=alt.X('zones:N', title='Zones',
                sort=alt.EncodingSortField('insurance_penetration', op='sum', order='descending')),
        y=alt.Y('insurance_penetration:Q', title='Insurance Penetration (%)'),
        color=alt.Color('zones:N', 
                       scale=zone_colors,
                       legend=None), 
        opacity=alt.Opacity('year:O',
                           scale=alt.Scale(domain=sorted(final_merged_data['year'].unique()), 
                                         range=[1.0, 0.7, 0.4, 0.2]),
                           legend=alt.Legend(title='Year', orient='right')),
        xOffset='year:O'
    )
    .properties(
        title='Insurance Penetration by Zone and Year',
        width=400,
        height=300
    )
)
# Combine 
farmer_count_rate = alt.hconcat(chart_farmers, chart_penetration).resolve_scale(
    color='independent',
    opacity='shared'
)

farmer_count_rate

alt.HConcatChart(...)

In [31]:
# To separate the seasons of each year 
def insurance_heatmap_seasons_zones(df):
    df['season_name'] = df['season_flag'].map({0: 'Rabi', 1: 'Kharif'})
    df['year_season'] = df['year'].astype(str) + ' ' + df['season_name']
    
    heatmap = alt.Chart(df).mark_rect().encode(
        x=alt.X('year_season:N', title='Year-Season', axis=alt.Axis(labelAngle=0)),
        y=alt.Y('zones:N', title='Zone', sort='-x'),
        color=alt.Color('mean(insurance_penetration):Q', 
                       title='Insurance Penetration %',
                       scale=alt.Scale(scheme='greens'))
    ).properties(
        width=700,
        height=400,
        title='Insurance Penetration Heatmap by Zone and Season'
    )
    
    return heatmap

insurance_heatmap_seasons_zones(final_merged_data)

alt.Chart(...)

In [35]:
# State vs GOI premium share 
# Aggregate by state 
state_shares = final_merged_data.groupby('state_name').agg({
    'goi_share': 'sum',
    'state_share': 'sum'
}).reset_index()

state_shares['total_share'] = state_shares['goi_share'] + state_shares['state_share']
state_shares['goi_pct'] = state_shares['goi_share'] / state_shares['total_share']
state_shares['state_pct'] = state_shares['state_share'] / state_shares['total_share']

# Convert to long format
shares_long_ne = state_shares.melt(
    id_vars='state_name',
    value_vars=['goi_pct', 'state_pct'],
    var_name='share_type',
    value_name='share_value'
)

# Barchart 
chart_goi_states = alt.Chart(shares_long_ne).mark_bar().encode(
    x=alt.X('state_name:N', 
            axis=alt.Axis(labelAngle=-45), 
            title='State', 
            sort=alt.EncodingSortField('goi_pct', op='max')), 
    y=alt.Y('share_value:Q', stack='normalize', title='Share (%)', axis=alt.Axis(format='%')),
    color=alt.Color('share_type:N', title='Share Type', 
                   scale=alt.Scale(domain=['goi_pct', 'state_pct'], 
                                  range=['#ff7f0e', '#1f77b4']),
                    legend=alt.Legend(title='Share Type',
                                   labelExpr="{'goi_pct': 'Government of India Share', 'state_pct':'State Share'}[datum.label]")),
).properties(
    title='GOI vs State Premium Share - All States',
    width=700,
    height=400
)

chart_goi_states

alt.Chart(...)

In [33]:
# For NE states only 
northeast_states = merged_final[merged_final['zones'] == 'North East Zone']

state_shares_ne = northeast_states.groupby('state_name').agg({
    'goi_share': 'sum',
    'state_share': 'sum'
}).reset_index()

state_shares_ne['total_share'] = state_shares_ne['goi_share'] + state_shares_ne['state_share']
state_shares_ne['goi_pct'] = state_shares_ne['goi_share'] / state_shares_ne['total_share']
state_shares_ne['state_pct'] = state_shares_ne['state_share'] / state_shares_ne['total_share']

shares_long_ne = state_shares_ne.melt(
    id_vars='state_name',
    value_vars=['goi_pct', 'state_pct'],
    var_name='share_type',
    value_name='share_value'
)

chart_ne_states = alt.Chart(shares_long_ne).mark_bar().encode(
    x=alt.X('state_name:N', 
            axis=alt.Axis(labelAngle=0), 
            title='State', 
            sort=alt.EncodingSortField('goi_pct', op='max')), 
    y=alt.Y('share_value:Q', stack='normalize', title='Share (%)', axis=alt.Axis(format='%')),
    color=alt.Color('share_type:N', title='Share Type', 
                   scale=alt.Scale(domain=['goi_pct', 'state_pct'], 
                                  range=['#ff7f0e', '#1f77b4']),
                    legend=alt.Legend(title='Share Type',
                                   labelExpr="{'goi_pct': 'Government of India Share', 'state_pct':'State Share'}[datum.label]")),
).properties(
    title='GOI vs State Premium Share - North East Zone States',
    width=300,
    height=400
)

chart_ne_states

alt.Chart(...)

In [37]:
# Loanee Farmer ratio 
zone_farmer_ratio = final_merged_data.groupby('zones').agg({
    'farmer_count': 'sum',
    'loanee': 'sum'
}).reset_index()

zone_farmer_ratio['farmer_lonee_ratio'] = (
    zone_farmer_ratio['loanee'] / zone_farmer_ratio['farmer_count']
)
zone_farmer_ratio['farmer_lonee_ratio'] = zone_farmer_ratio['farmer_lonee_ratio'].replace([np.inf, -np.inf], np.nan)

# color scale 
color_scale = alt.Scale(
    domain=list(custom_colors.keys()),
    range=list(custom_colors.values())
)

# Create simple bar chart
chart = alt.Chart(zone_farmer_ratio).mark_bar().encode(
    x=alt.X('zones:N', title='Zone', sort='-y'),
    y=alt.Y('farmer_lonee_ratio:Q', title='Loanee to Farmer Ratio'),
    color=alt.Color('zones:N', scale=color_scale)
).properties(
    width=300,
    height=400,
    title='Loanee to farmer Ratio by Zone'
)

chart

alt.Chart(...)

In [ ]:
# Female ration 
# Subset to show female ratio in the last year in data 
df_2022 = final_merged_data.query("year == 2022 and season_flag == 0")

# Separate groups
ne_df = df_2022[df_2022['zones'] == 'North East Zone']
other_zones_df = df_2022[df_2022['zones'] != 'North East Zone']

# Averages
avg_other_zones = other_zones_df['female'].mean()
avg_india = df_2022['female'].mean()

# Base chart for NE states
base = alt.Chart(ne_df).mark_point(
    size=100,
    filled=True
).encode(
    x=alt.X('state_name:N', axis=alt.Axis(labelAngle=0), title='State', sort='-y'),
    y=alt.Y('female:Q', title='% Female Farmers'),
    color=alt.value('#1f77b4'),
    tooltip=['state_name', 'female']
)

# Compute approximate horizontal placement for averages
x_pos = len(ne_df) / 2 * 80

# Average of other zones
avg_other_df = pd.DataFrame({'label': ['Other Zones'], 'female': [avg_other_zones]})
avg_other_dot = alt.Chart(avg_other_df).mark_point(
    shape='square',
    size=150,
    color='orange'
).encode(
    x=alt.value(x_pos),
    y='female:Q',
    tooltip=[alt.Tooltip('female:Q', title='% Female (Other Zones Avg)')]
)

# Used LLM to udnerstand how to insert floating label for "Other Zone" and "India"
avg_other_label = alt.Chart(avg_other_df).mark_text(
    align='left',
    dx=10,
    dy=-4,
    fontSize=12,
    color='orange'
).encode(
    x=alt.value(x_pos),
    y='female:Q',
    text='label:N'
)

# India average. Used LLMs to understand how to insert shapes of different color in mark_point. 
avg_india_df = pd.DataFrame({'label': ['India'], 'female': [avg_india]})
avg_india_dot = alt.Chart(avg_india_df).mark_point(
    shape='triangle-up',
    size=150,
    color='red'
).encode(
    x=alt.value(x_pos),
    y='female:Q',
    tooltip=[alt.Tooltip('female:Q', title='% Female (India Avg)')]
)

# Floating label for India
avg_india_label = alt.Chart(avg_india_df).mark_text(
    align='left',
    dx=10,
    dy=-4,
    fontSize=12,
    color='red'
).encode(
    x=alt.value(x_pos),
    y='female:Q',
    text='label:N'
)

# Combine
Female_farmer = (base + avg_other_dot + avg_other_label + avg_india_dot + avg_india_label).properties(
    title='% Female Farmers in North East Zone States (2022)',
    width=600,
    height=400
).configure_axisX(labelAngle=-45)

Female_farmer


alt.LayerChart(...)